In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from scripts.hydraulic import hydr

import io
import PIL

# <center/> Расчет нестационарного течения жидкости в нефтепроводе

In [2]:
# Исходные данные
L = 100 # Длина участка, км 
dx = 1 # Шаг расчета параметров, км
c = 1000 # Скорость распространения волн давления в трубопроводе(для нефти примерное значение, зависит от многих факторов), м/с
d = 1000 # Внутренний диаметр, мм
D = 1020 # Наружный диаметр, мм
rho = 1000 # Плотность жидкости, кг/м^3
Ny = 1 # Кинематическая вязкость, сСт
w0 = 2.7 # Скорость жидкости в трубопроводе в стационарном режиме, м/с
a = 220 # Коэффициент аппроксимации характеристики насоса, м
b = 8.88e-07 # Коэффициент аппроксимации характеристики насоса, ч^2/м^5
hp = 50 # Подпор в начале участка, м
tao = 250 # Период времени для расчета параметров жидкости вы трубопроводе, с
pressureRiseTime = 50 # Время, в которое происходит повышение давления, начиная с начала отсчета, с
deltaP = 2.5 # Величина повышения давления, МПа
xsi = 0.21 # Коэффициент местного сопротивления клапана
Svalve = np.pi * 0.1**2 / 4 # Площадь клапана, м^2
valveCoord = 80 # Координата установки предохранительного клапана, км
PstartOpening = 2.5 # Давление начала открытия предохранительного клапана, МПа
PendOpening = 1.2 * PstartOpening # Давление конца открытия(полного открытия) предохранительного клапана, МПа

In [3]:
# Инициализация расчетного класса
hydr = hydr(d=d,
            D=D,
            Ny=Ny,
            rho=rho,
            dx=dx,
            c=c,
            a=a,
            b=b,
            hp=hp,
            xsi=xsi,
            Svalve=Svalve,
            PstartOpening=PstartOpening,
            PendOpening=PendOpening
            )

In [4]:
# Временной интервал измерения, с
dt = dx * 1000 / c

Q = w0 * np.pi * d**2 / 4 / 10**6 * 3600 # Расход в м^3/ч
P0 = rho * 9.81 * (hp+3*(a-b*Q**2)) / 10**6 # Начальное давление, МПа

# Задаем таблицы скорости и давления
flowRate = pd.DataFrame(columns=range(0, int(L*1000) + 1, int(dx*1000)), index=[0], data=w0)

pressure = pd.DataFrame(columns=range(0, int(L*1000) + 1, int(dx*1000)), index=[0], data=P0)

# Расчет падения давления по длине трубопровода
for i, x in enumerate(pressure.columns[1:]):
    pressure.iloc[0, i+1] = pressure.iloc[0, 0] - hydr.i(w0)*x/10**6
    
pressure = pressure.round(3)

# Количество строк для добавления
strCount = int(np.ceil(tao / dt))

# Границы участков
leftBound = 0
rightBound = len(pressure.columns) - 1

In [5]:
traceListPressure = [
    go.Scatter(visible=True, x=pressure.columns/1000, y=pressure.iloc[0, :], mode='lines', name=0)
]

traceListRate = [
    go.Scatter(visible=True, x=flowRate.columns/1000, y=flowRate.iloc[0, :], mode='lines', name=0)
]

## Animation

traceListPressureAnime = [
    go.Scatter(x=pressure.columns/1000, y=pressure.iloc[0, :], mode='lines', name=0)
]

traceListRateAnime = [
    go.Scatter(x=flowRate.columns/1000, y=flowRate.iloc[0, :], mode='lines', name=0)
]

##

KvalveLst = [] # Список степеней открытия клапана в каждый момент времени

# Расчет давления и скорости для указанного времени с заданным интервалом по длине трубопровода
for counter in range(1, strCount + 1):
    pressure.loc[counter * dt, :] = 0
    flowRate.loc[counter * dt, :] = 0
    
    for i, x in enumerate(pressure.columns):
        
        # Левая граница
        
        if i == leftBound:
            # Параметры рассматриваемой точки
            pressure.iloc[-1, i] = hydr.Pc(Pb=pressure.iloc[-2, i + 1], wb=flowRate.iloc[-2, i + 1], leftBound=True)
            flowRate.iloc[-1, i] = hydr.wc(Pb=pressure.iloc[-2, i + 1], wb=flowRate.iloc[-2, i + 1], leftBound=True)
            
        # Правая граница
        
        elif i == rightBound: 
            # Параметры рассматриваемой точки
            
            # Учитываем время изменения давления
            if pressure.index[-1] == pressureRiseTime:
                Pc = pressure.iloc[-1, i] = pressure.iloc[-2, rightBound] + deltaP
            else:
                Pc = pressure.iloc[-1, i] = pressure.iloc[-2, rightBound]
            
            flowRate.iloc[-1, i] = hydr.wc(Pa=pressure.iloc[-2, i - 1], wa=flowRate.iloc[-2, i - 1], rightBound=True, Pc=Pc)
        
        # Предохранительный клапан
        
        # Предыдущая точка
        
        elif (x == (valveCoord-dx) * 10**3) & (counter >= 2):
             
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = hydr.wc(pressure.iloc[-3, i],
                         pressure.iloc[-3, i + 2],
                         flowRate.iloc[-3, i],
                         flowRate.iloc[-3, i + 2],
                         valve=True
                         )[0]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]
                
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)

        # Следующая точка
        
        elif (x == (valveCoord+dx) * 10**3) & (counter >= 2):
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = hydr.wc(pressure.iloc[-3, i - 2],
                         pressure.iloc[-3, i],
                         flowRate.iloc[-3, i - 2],
                         flowRate.iloc[-3, i],
                         valve=True
                         )[1]
            
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
                
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)
                
        # Сам клапан
        
        elif x == valveCoord * 10**3:
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]

            # Параметры рассматриваемой точки
            Pc = pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb, valve=True)
            wprev, wnext, marker = hydr.wc(Pa, Pb, wa, wb, valve=True)
            
            flowRate.iloc[-1, i] = wprev 
            
            # Степень открытия клапана
            if Pc - 0.101325 < PstartOpening:
                KvalveLst.append(0)
                
            elif Pc - 0.101325 > PendOpening:
                KvalveLst.append(1)
                
            else:
                eta = (Pc - 0.101325 - PstartOpening) \
                    / (PendOpening - PstartOpening)
                
                KvalveLst.append(eta)
            
        # Промежуточные точки
        
        else:
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]

            # Параметры рассматриваемой точки
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)
            
    if marker:
        flowRatey = flowRate.loc[counter * dt, :(valveCoord-dx)*1000].to_list() + [wprev, wnext] + flowRate.loc[counter * dt, (valveCoord+dx)*1000:].to_list()
        flowRatex = flowRate.loc[counter * dt, :(valveCoord-dx)*1000].index.to_list() + [valveCoord*1000, valveCoord*1000] + flowRate.loc[counter * dt, (valveCoord+dx)*1000:].index.to_list()
        
        traceListRate.append(go.Scatter(visible=False, x=np.array(flowRatex)/1000, y=flowRatey, mode='lines', name=counter * dt))
        traceListRateAnime.append(go.Scatter(x=np.array(flowRatex)/1000, y=flowRatey, mode='lines', name=counter * dt))
    else:
        traceListRate.append(go.Scatter(visible=False, x=flowRate.columns/1000, y=flowRate.loc[counter * dt, :], mode='lines', name=counter * dt))
        traceListRateAnime.append(go.Scatter(x=flowRate.columns/1000, y=flowRate.loc[counter * dt, :], mode='lines', name=counter * dt))
        
    traceListPressure.append(go.Scatter(visible=False, x=pressure.columns/1000, y=pressure.loc[counter * dt, :], mode='lines', name=counter * dt))
    traceListPressureAnime.append(go.Scatter(x=pressure.columns/1000, y=pressure.loc[counter * dt, :], mode='lines', name=counter * dt))






display(pressure)
display(flowRate)

0       1000    2000    3000    4000    5000    6000    7000    8000    \
0     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
1     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
2     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
3     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
4     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
246   5.913   5.879   5.839   5.804   5.767   5.732   5.698   5.663   5.630   
247   5.913   5.873   5.838   5.801   5.767   5.732   5.697   5.664   5.629   
248   5.907   5.872   5.835   5.801   5.766   5.732   5.698   5.663   5.630   
249   5.906   5.869   5.835   5.800   5.766   5.732   5.698   5.664   5.628   
250   5.904   5.869   5.834   5.800   5.766   5.732   5.698   5.663   5.630   

     9000    ...  91000   92000   93000   94000   95000   96000   97000   \
0     5.000  ...   0.972   0.923   0.874   0.825   0.776   0.727   0.678   
1     5.000  ...   0.973   0.923   0.874   0.825   0.776   0.727   0.678   
2     5.000  ...   0.972   0.924   0.874   0.825   0.776   0.727   0.678   
3     5.000  ...   0.973   0.923   0.874   0.825   0.776   0.727   0.678   
4     5.000  ...   0.972   0.924   0.874   0.825   0.776   0.727   0.677   
..      ...  ...     ...     ...     ...     ...     ...     ...     ...   
246   5.596  ...   3.063   3.057   3.056   3.052   3.049   3.042   3.049   
247   5.596  ...   3.062   3.057   3.053   3.053   3.046   3.043   3.037   
248   5.594  ...   3.061   3.058   3.054   3.047   3.047   3.041   3.037   
249   5.596  ...   3.060   3.058   3.052   3.048   3.042   3.041   3.035   
250   5.594  ...   3.061   3.054   3.052   3.047   3.042   3.036   3.035   

     98000   99000   100000  
0     0.629   0.580    0.53  
1     0.629   0.580    0.53  
2     0.629   0.579    0.53  
3     0.628   0.579    0.53  
4     0.628   0.579    0.53  
..      ...     ...     ...  
246   3.042   3.036    3.03  
247   3.043   3.036    3.03  
248   3.031   3.037    3.03  
249   3.031   3.025    3.03  
250   3.029   3.024    3.03  

[251 rows x 101 columns]

0       1000    2000    3000    4000    5000    6000    7000    8000    \
0     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
1     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
2     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
3     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
4     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
246   2.244   2.244   2.250   2.252   2.255   2.254   2.256   2.255   2.255   
247   2.244   2.250   2.251   2.254   2.255   2.256   2.255   2.255   2.255   
248   2.250   2.251   2.254   2.254   2.255   2.256   2.255   2.255   2.255   
249   2.251   2.254   2.254   2.255   2.255   2.255   2.256   2.255   2.256   
250   2.254   2.254   2.255   2.255   2.255   2.255   2.255   2.257   2.255   

     9000    ...  91000   92000   93000   94000   95000   96000   97000   \
0     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
1     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
2     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
3     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
4     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.701   
..      ...  ...     ...     ...     ...     ...     ...     ...     ...   
246   2.256  ...   0.604   0.608   0.609   0.611   0.608   0.613   0.620   
247   2.255  ...   0.610   0.607   0.609   0.609   0.614   0.611   0.615   
248   2.256  ...   0.608   0.611   0.607   0.612   0.612   0.616   0.614   
249   2.255  ...   0.610   0.608   0.614   0.610   0.614   0.615   0.619   
250   2.255  ...   0.608   0.613   0.611   0.616   0.613   0.617   0.618   

     98000   99000   100000  
0     2.700   2.700   2.700  
1     2.700   2.700   2.701  
2     2.700   2.701   2.701  
3     2.701   2.701   2.701  
4     2.701   2.701   2.701  
..      ...     ...     ...  
246   0.623   0.619   0.623  
247   0.623   0.626   0.622  
248   0.618   0.626   0.629  
249   0.617   0.621   0.630  
250   0.622   0.621   0.613  

[251 rows x 101 columns]

In [6]:
# Графическое отображение

# Давление
num_steps = len(pressure.index)


fig = go.Figure(data=traceListPressure)

steps = []
for i in range(num_steps):
    step = dict(
        method = 'restyle',
        args = ['visible', [False] * len(fig.data)],
    )
    step['args'][1][i] = True
    steps.append(step)

sliders = [dict(
    currentvalue = {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 10}},
    len = 0.9,
    x = 0.1,
    pad = {"b": 10, "t": 50},
    steps = steps,
)]

fig.update_layout(
    title='Распределение давления',
    xaxis_title='X, км',
    yaxis_title='P, МПа',
    height=800,
    width=1000,
    yaxis_range=[0, 8]
)

fig.layout.sliders = sliders

#fig.write_html('pressureDestribution.html')
fig.show()

In [7]:
# Скорость
num_steps = len(flowRate.index)



fig = go.Figure(data=traceListRate)

steps = []
for i in range(num_steps):
    step = dict(
        method = 'restyle',
        args = ['visible', [False] * len(fig.data)],
    )
    step['args'][1][i] = True
    steps.append(step)

sliders = [dict(
    currentvalue = {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 10}},
    len = 0.9,
    x = 0.1,
    pad = {"b": 10, "t": 50},
    steps = steps,
)]

fig.update_layout(
    title='Распределение скорости',
    xaxis_title='X, км',
    yaxis_title='w, м/с',
    height=800,
    width=1000,
    yaxis_range=[0, 5]
)

fig.layout.sliders = sliders

#fig.write_html('flowRateDestribution.html')
fig.show()

In [8]:
fig = make_subplots(2)

fig.add_trace(
    traceListPressureAnime[0],
    row=1,
    col=1
)

fig.add_trace(
    traceListRateAnime[0],
    row=2,
    col=1
)

num_steps = len(flowRate.index) - 1
frames = []

for i in range(1, num_steps + 1):
    frames.append(
        go.Frame(data=[traceListPressureAnime[i], traceListRateAnime[i]], traces=[0, 1], name=str(i))
    )
    
fig.frames = frames

fig.update_layout(legend_orientation="h",
                  legend=dict(x=.5, xanchor="center"),
                  updatemenus=[dict(direction="left", x=0.5, xanchor="center", y=0,
                                    type="buttons", buttons=[dict(label="►", method="animate", args=[None, {"frame": {"duration": 120, 
                                                                                                                      "redraw": False},
                                                                                                            "fromcurrent": True, 
                                                                                                            "transition": {"duration": 5}}]),
                                                             dict(label="❚❚", method="animate", args=[[None], {"frame": {"duration": 0, "redraw": False},
                                                                                                               "mode": "immediate",
                                                                                                               "transition": {"duration": 0}}])])],
                  margin=dict(l=0, r=0, t=0, b=0))


fig.update_layout(
    height=800,
    width=1500,
    showlegend=False
)

fig.update_xaxes(title=r'$$x, км$$', col=1, row=1)
fig.update_yaxes(title=r'$$P, МПа$$', range=[0, 8], col=1, row=1)
fig.update_yaxes(title=r'$$\upsilon,\text{м/с}$$', range=[-1, 4], col=1, row=2)

def frame_args(duration):
    return {
            "frame": {"duration": duration + 115, 'redraw': False},
            "fromcurrent": True,
            "transition": {"duration": duration},
        }

sliders = [
            {
                'currentvalue': {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 20}},
                "pad": {"b": 10, "t": 60},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "steps": [
                    {
                        "args": [[f.name], frame_args(5)],
                        "label": str(k),
                        "method": "animate",
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]

fig.update_xaxes(title_font_size=20)
fig.update_yaxes(title_font_size=20)

fig.layout.sliders = sliders

fig.show()

In [9]:
frames = []
for s, fr in enumerate(fig.frames):
    # set main traces to appropriate traces within plotly frame
    fig.update(data=fr.data)
    # move slider to correct place
    fig.layout.sliders[0].update(active=s)
    # generate image of current state
    frames.append(PIL.Image.open(io.BytesIO(fig.to_image(format="png"))))
    
# create animated GIF
frames[0].save(
        "test.gif",
        save_all=True,
        append_images=frames[1:],
        optimize=True,
        duration=125,
        loop=0,
    )

In [10]:
fig1 = go.Figure()

fig1.add_trace(
    go.Scatter(
        x=pressure.index,
        y=np.array(KvalveLst) * 100,
        name='$$\delta p_{н.о.}$$' + str(PstartOpening)
    )
)

fig1.update_layout(
    height=500,
    width=750,
    xaxis_title='$$t, c$$',
    yaxis_title=r'$$\eta, \text{%}$$',
    yaxis_range=[0, 100],
    showlegend=True
)

fig1.update_xaxes(title_font_size=30)
fig1.update_yaxes(title_font_size=30)

fig1.show()